In [9]:
from kaggle_environments.envs.halite.helpers import *
from random import choice
from kaggle_environments import evaluate

In [10]:
%%writefile imitation_learning.py
from kaggle_environments.envs.halite.helpers import *

import numpy as np
import torch
import torch.nn as nn
import torch.nn.functional as F
from torch.distributions.categorical import Categorical
import time

device = "cuda" if torch.cuda.is_available() else "cpu"

class TorusConv2d(nn.Module):
    def __init__(self, input_dim, output_dim, kernel_size, bn):
        super().__init__()
        self.edge_size = (kernel_size[0] // 2, kernel_size[1] // 2)
        self.conv = nn.Conv2d(input_dim, output_dim, kernel_size=kernel_size)
        self.bn = nn.BatchNorm2d(output_dim) if bn else None

    def forward(self, x):
        h = torch.cat([x[:,:,:,-self.edge_size[1]:], x, x[:,:,:,:self.edge_size[1]]], dim=3)
        h = torch.cat([h[:,:,-self.edge_size[0]:], h, h[:,:,:self.edge_size[0]]], dim=2)
        h = self.conv(h)
        h = self.bn(h) if self.bn is not None else h
        return h


class HaliteNet(nn.Module):
    def __init__(self):
        super().__init__()
        layers, filters = 16, 128
        self.conv0 = TorusConv2d(9, filters, (3, 3), True)
        self.blocks = nn.ModuleList([TorusConv2d(filters, filters, (3, 3), True) for _ in range(layers)])
        
        self.head_ships_p = nn.Conv2d(filters, 6, kernel_size=1, stride=1)
        self.head_shipyards_p = nn.Conv2d(filters, 2, kernel_size=1, stride=1)
        self.head_v = nn.Linear(filters * 2, 1, bias=False)

    def forward(self, x, action=None):
        h = F.relu_(self.conv0(x))
        for block in self.blocks:
            h = F.relu_(h + block(h))
        ########################## /!\ ###########################
        # Do we concentrate around the ships of current player ? #
        ########################## /!\ ###########################
        #h_head = (h * x[:,:1]).view(h.size(0), h.size(1), -1).sum(-1)
        h_head = h.view(h.size(0), h.size(1), -1).sum(-1)
        h_avg = h.view(h.size(0), h.size(1), -1).mean(-1)
        ships_p = self.head_ships_p(h)
        shipyards_p = self.head_shipyards_p(h)
        v = torch.tanh(self.head_v(torch.cat([h_head, h_avg], 1)))
        
        ships_logits = ships_p.reshape(-1,6,21*21)
        shipyards_logits = shipyards_p.reshape(-1,2,21*21)
        action = torch.cat([ships_logits, shipyards_logits], 1)
   
        return action

agent = HaliteNet().to(device)
agent.load_state_dict(torch.load('../input/halite-iml/weights1.pt'))
agent.eval()
def get_observation(raw_obs, configuration):
    board = Board(raw_observation=raw_obs, \
                  raw_configuration=configuration)

    obs = torch.zeros((9,\
                       board.configuration.size,\
                       board.configuration.size))

    current_player = board.current_player
    opponents = board.opponents
    obs[7] = current_player.halite/5000
    obs[8] = opponents[0].halite/5000
    # Halite map
    for c in board.cells:
        obs[(0,)+tuple(c)] = board.cells[c].halite/1000

    # Ships map
    for s in current_player.ships:
        obs[(1,)+tuple(s.position)] = 1
    for i,o in enumerate(opponents):
        for s in o.ships:
            obs[(i+2,)+tuple(s.position)] = 1

    # Ships halite map
    for s in current_player.ships:
        obs[(3,)+tuple(s.position)] = s.halite/500
    for i,o in enumerate(opponents):
        for s in o.ships:
            obs[(i+4,)+tuple(s.position)] = s.halite/500

    # Shipyard map
    for s in current_player.shipyards:
        obs[(5,)+tuple(s.position)] = 1
    for i,o in enumerate(opponents):
        for s in o.shipyards:
            obs[(i+6,)+tuple(s.position)] = 1

    return obs

def submission(obs, conf):
    counter = obs['step']
    if counter == 75:
        print("changing model")
        agent.load_state_dict(torch.load('../input/halite-iml/weights2.pt'))
        agent.eval()
    if counter == 325:
        print("changing model")
        agent.load_state_dict(torch.load('../input/halite-iml/weights3.pt'))
        agent.eval()
    
    observation = get_observation(obs, conf).to(device)
    prev_time = time.time()
    actions = torch.cat([agent(observation.unsqueeze(0))[0][:6].T.argmax(1),\
                          agent(observation.unsqueeze(0))[0][6:].T.argmax(1)])
    
    raw_actions = agent(observation.unsqueeze(0))[0][:6]
    finish_time = time.time()
    #print(f"Time taken by HaliteNet : {finish_time-prev_time}")
    previous_board = Board(raw_observation=obs,\
                            raw_configuration=conf)
    current_player_ships_ordered = previous_board.current_player.ships
    current_player_ships_ordered.sort(
        reverse=True,
        key=lambda s : s.halite
    )
    locations_map = np.zeros((21,21,1))
    for sy in previous_board.current_player.shipyards:
        a_id = 21*21 + sy.position.x*21+sy.position.y
        if actions[a_id]:
            sy.next_action = ShipyardAction.SPAWN

            if previous_board.current_player.halite >= 500:
                locations_map[sy.position] = 1

    for s in current_player_ships_ordered:
        a_id = s.position.x*21+s.position.y

        _, indices = torch.sort(raw_actions[:,a_id], descending=True)
        for action in indices:
            if action and action != 5:
                action = ShipAction.moves()[action-1]
                new_pos = s.cell.neighbor(action.to_point())
                if not locations_map[new_pos.position]:
                    locations_map[new_pos.position] = 1
                    s.next_action = action
                    break
            elif action == 5:
                if s.halite + previous_board.current_player.halite >= 500:
                    s.next_action = ShipAction.CONVERT
                    break
            else:
                new_pos = s.position
                if not locations_map[new_pos]:
                    locations_map[new_pos] = 1
                    break
    #print(len(previous_board.current_player.ships))
    return previous_board.current_player.next_actions

Overwriting imitation_learning.py


From [halite-swarm-intelligence-playground-edition](https://www.kaggle.com/code/yegorbiryukov/halite-swarm-intelligence-playground-edition)

In [11]:
%%writefile swarm.py
# for Debug previous line (%%writefile submission.py) should be commented out, uncomment to write submission.py

#FUNCTIONS###################################################
def set_map_and_average_halite(s_env):
    """
        set average amount of halite per halite source
        and map as two dimensional array of objects and set amounts of halite in each cell
    """
    s_env["map"] = []
    halite_sources_amount = 0
    halite_total_amount = 0
    for x in range(conf.size):
        s_env["map"].append([])
        for y in range(conf.size):
            s_env["map"][x].append({
                # value will be ID of owner
                "shipyard": None,
                # value will be ID of owner
                "ship": None,
                # value will be amount of halite
                "ship_cargo": None,
                # amount of halite
                "halite": s_env["obs"].halite[conf.size * y + x]
            })
            if s_env["map"][x][y]["halite"] > 0:
                halite_total_amount += s_env["map"][x][y]["halite"]
                halite_sources_amount += 1
    s_env["average_halite"] = halite_total_amount / halite_sources_amount

def update_map(s_env):
    """
        update locations of ships and shipyards on the map,
        get lists of coords of Swarm's units,
        get targets for "torpedoes"
    """
    global torpedo_targets
    torpedo_targets = []
    # arrays of (x, y) coords
    s_env["swarm_shipyards_coords"] = []
    s_env["swarm_ships_coords"] = []
    # place on the map locations of units of every player
    for player in range(len(s_env["obs"].players)):
        # set torpedo targets
        target_index = 0
        for i in range(len(torpedo_targets)):
            while (target_index < len(torpedo_targets) and
                    s_env["obs"].players[player][0] < torpedo_targets[target_index]["halite"]):
                target_index += 1
        torpedo_targets.insert(target_index, {
            "player": player,
            "shipyards": [],
            "halite": s_env["obs"].players[player][0]
        })
        # place on the map locations of every shipyard of the player
        shipyards = list(s_env["obs"].players[player][1].values())
        for shipyard in shipyards:
            x = shipyard % conf.size
            y = shipyard // conf.size
            # place shipyard on the map
            s_env["map"][x][y]["shipyard"] = player
            torpedo_targets[target_index]["shipyards"].append({"x": x, "y": y})
            if player == s_env["obs"].player:
                s_env["swarm_shipyards_coords"].append((x, y))
        # place on the map locations of every ship of the player
        ships = list(s_env["obs"].players[player][2].values())
        for ship in ships:
            x = ship[0] % conf.size
            y = ship[0] // conf.size
            # place ship on the map
            s_env["map"][x][y]["ship"] = player
            s_env["map"][x][y]["ship_cargo"] = ship[1]
            if player == s_env["obs"].player:
                s_env["swarm_ships_coords"].append((x, y))

def get_c(c):
    """ get coordinate, considering donut type of the map """
    return c % conf.size

def clear(x, y, player, game_map):
    """ check if cell is safe to move in """
    # if there is no shipyard, or there is player's shipyard
    # and there is no ship
    if ((game_map[x][y]["shipyard"] == player or game_map[x][y]["shipyard"] == None) and
            game_map[x][y]["ship"] == None):
        return True
    return False

def get_closest_coords(x_initial, y_initial, s_env, coords_list):
    """ get from coords_list x and y closest to x_initial and y_initial """
    closest_coords_index = 0
    min_distance = None
    for i in range(len(coords_list)):
        to_x = coords_list[i]["x"]
        to_y = coords_list[i]["y"]
        # choose x route
        if x_initial > to_x:
            normal_route_x = x_initial - to_x
            donut_route_x = conf.size - x_initial + to_x
        else:
            normal_route_x = to_x - x_initial
            donut_route_x = conf.size - to_x + x_initial
        # x distance to shipyard
        x_dist = donut_route_x if donut_route_x < normal_route_x else normal_route_x
        # choose y route
        if y_initial > to_y:
            normal_route_y = y_initial - to_y
            donut_route_y = conf.size - y_initial + to_y
        else:
            normal_route_y = to_y - y_initial
            donut_route_y = conf.size - to_y + y_initial
        # y distance to shipyard
        y_dist = donut_route_y if donut_route_y < normal_route_y else normal_route_y
        dist = x_dist + y_dist
        if min_distance == None or dist < min_distance:
            min_distance = dist
            closest_coords_index = i
    return coords_list[closest_coords_index]

def move_to_cell(to_x, to_y, x_initial, y_initial, actions, s_env, ship_index):
    """ move ship to cell with to_x and to_y coords, if possible """
    ship_id = s_env["ships_keys"][ship_index]
    ship_cargo = s_env["ships_values"][ship_index][1]
    
    # choose x route
    if x_initial > to_x:
        normal_route_x = x_initial - to_x
        donut_route_x = conf.size - x_initial + to_x
        # x direction to shipyard
        x_dir = "WEST"
    else:
        normal_route_x = to_x - x_initial
        donut_route_x = conf.size - to_x + x_initial
        x_dir = "EAST"
    # x distance to shipyard
    x_dist = donut_route_x if donut_route_x < normal_route_x else normal_route_x
    
    # choose y route
    if y_initial > to_y:
        normal_route_y = y_initial - to_y
        donut_route_y = conf.size - y_initial + to_y
        # y direction to shipyard
        y_dir = "NORTH"
    else:
        normal_route_y = to_y - y_initial
        donut_route_y = conf.size - to_y + y_initial
        y_dir = "SOUTH"
    # y distance to shipyard
    y_dist = donut_route_y if donut_route_y < normal_route_y else normal_route_y

    # get possible directions
    for direction in directions_list:
        if direction["direction"] == x_dir:
            x = direction["x"](x_initial)
        elif direction["direction"] == y_dir:
            y = direction["y"](y_initial)

    # choose direction
    # if this ship is not a "torpedo"
    if ships_data[s_env["ships_keys"][ship_index]]["target_coords"] == None:
        if x_dist > y_dist:
            if (clear(x, y_initial, s_env["obs"].player, s_env["map"]) and
                    not hostile_ship_near(x, y_initial, s_env["obs"].player, s_env["map"], ship_cargo)):
                s_env["map"][x_initial][y_initial]["ship"] = None
                s_env["map"][x][y_initial]["ship"] = s_env["obs"].player
                actions[ship_id] = x_dir
                return True
        else:
            if (clear(x_initial, y, s_env["obs"].player, s_env["map"]) and
                    not hostile_ship_near(x_initial, y, s_env["obs"].player, s_env["map"], ship_cargo)):
                s_env["map"][x_initial][y_initial]["ship"] = None
                s_env["map"][x_initial][y]["ship"] = s_env["obs"].player
                actions[ship_id] = y_dir
                return True
    # if this ship is a "torpedo"
    else:
        if x_dist > y_dist:
            if s_env["map"][x][y_initial]["ship"] == None:
                s_env["map"][x_initial][y_initial]["ship"] = None
                s_env["map"][x][y_initial]["ship"] = s_env["obs"].player
                actions[ship_id] = x_dir
                return True
        else:
            if s_env["map"][x_initial][y]["ship"] == None:
                s_env["map"][x_initial][y_initial]["ship"] = None
                s_env["map"][x_initial][y]["ship"] = s_env["obs"].player
                actions[ship_id] = y_dir
                return True
    return False

def return_to_shipyard(x_initial, y_initial, actions, s_env, ship_index):
    """ return to shipyard's coords """
    ship_id = s_env["ships_keys"][ship_index]
    ship_cargo = s_env["ships_values"][ship_index][1]
    # if ship is currently at shipyard's coords
    if x_initial == shipyard_coords["x"] and y_initial == shipyard_coords["y"]:
        # if there is no shipyard at shipyard's coords
        if (s_env["map"][x_initial][y_initial]["shipyard"] == None and
                (ship_cargo + s_env["swarm_halite"]) >= conf.convertCost):
            actions[ship_id] = "CONVERT"
            s_env["map"][x_initial][y_initial]["ship"] = None
            return True
        # if ship is going to move out from shipyard's coords
        else:
            global movement_tactics_index
            ships_data[ship_id]["moves_done"] = 0
            ships_data[ship_id]["ship_max_moves"] = 1
            ships_data[ship_id]["directions"] = movement_tactics[movement_tactics_index]["directions"]
            ships_data[ship_id]["directions_index"] = 0
            movement_tactics_index += 1
            if movement_tactics_index >= movement_tactics_amount:
                movement_tactics_index = 0
    else:
        # if ship has to return to shipyard's coords
        if ship_cargo >= s_env["return_threshold"]:
            return move_to_cell(
                shipyard_coords["x"], shipyard_coords["y"], x_initial, y_initial, actions, s_env, ship_index)
    return False

def move_ship(x_initial, y_initial, actions, s_env, ship_index):
    """ move the ship according to first acceptable tactic """
    if go_for_halite(x_initial, y_initial, s_env["ships_keys"][ship_index], actions, s_env, ship_index):
        return
    standard_patrol(x_initial, y_initial, s_env["ships_keys"][ship_index], actions, s_env, ship_index)

def go_for_halite(x_initial, y_initial, ship_id, actions, s_env, ship_index):
    """ ship will go to safe cell with enough halite, if it is found """
    # if current cell has enough halite
    if (s_env["map"][x_initial][y_initial]["halite"] > s_env["low_amount_of_halite"] and
            not hostile_ship_near(x_initial, y_initial, s_env["obs"].player, s_env["map"], s_env["ships_values"][ship_index][1])):
        most_halite = s_env["map"][x_initial][y_initial]["halite"]
    else:
        # biggest amount of halite among scanned cells
        most_halite = s_env["low_amount_of_halite"]
    direction = None
    for d in range(len(directions_list)):
        x = directions_list[d]["x"](x_initial)
        y = directions_list[d]["y"](y_initial)
        # if cell is safe to move in
        if (clear(x, y, s_env["obs"].player, s_env["map"]) and
                not hostile_ship_near(x, y, s_env["obs"].player, s_env["map"], s_env["ships_values"][ship_index][1])):
            # if current cell has more than biggest amount of halite
            if s_env["map"][x][y]["halite"] > most_halite:
                most_halite = s_env["map"][x][y]["halite"]
                direction = directions_list[d]["direction"]
                direction_x = x
                direction_y = y
    # if cell is safe to move in and has substantial amount of halite
    if most_halite > s_env["low_amount_of_halite"] and direction != None:
        actions[ship_id] = direction
        s_env["map"][x_initial][y_initial]["ship"] = None
        s_env["map"][direction_x][direction_y]["ship"] = s_env["obs"].player
        return True
    # if current cell has biggest amount of halite
    elif most_halite == s_env["map"][x_initial][y_initial]["halite"]:
        return True
    return False

def standard_patrol(x_initial, y_initial, ship_id, actions, s_env, ship_index):
    """ 
        ship will move in expanding circles clockwise or counterclockwise
        until reaching maximum radius, then radius will be minimal again
    """
    directions = ships_data[ship_id]["directions"]
    # set index of direction
    i = ships_data[ship_id]["directions_index"]
    for j in range(len(directions)):
        x = directions[i]["x"](x_initial)
        y = directions[i]["y"](y_initial)
        # if cell is ok to move in
        if (clear(x, y, s_env["obs"].player, s_env["map"]) and
                (s_env["map"][x][y]["shipyard"] == s_env["obs"].player or
                not hostile_ship_near(x, y, s_env["obs"].player, s_env["map"], s_env["ships_values"][ship_index][1]))):
            ships_data[ship_id]["moves_done"] += 1
            # apply changes to game_map, to avoid collisions of player's ships next turn
            s_env["map"][x_initial][y_initial]["ship"] = None
            s_env["map"][x][y]["ship"] = s_env["obs"].player
            # if it was last move in this direction
            if ships_data[ship_id]["moves_done"] >= ships_data[ship_id]["ship_max_moves"]:
                ships_data[ship_id]["moves_done"] = 0
                ships_data[ship_id]["directions_index"] += 1
                # if it is last direction in a list
                if ships_data[ship_id]["directions_index"] >= len(directions):
                    ships_data[ship_id]["directions_index"] = 0
                    ships_data[ship_id]["ship_max_moves"] += 1
                    # if ship_max_moves reached maximum radius expansion
                    if ships_data[ship_id]["ship_max_moves"] > max_moves_amount:
                        ships_data[ship_id]["ship_max_moves"] = 3
            actions[ship_id] = directions[i]["direction"]
            break
        else:
            # loop through directions
            i += 1
            if i >= len(directions):
                i = 0

def get_directions(i0, i1, i2, i3):
    """ get list of directions in a certain sequence """
    return [directions_list[i0], directions_list[i1], directions_list[i2], directions_list[i3]]

def hostile_ship_near(x, y, player, m, cargo):
    """ check if hostile ship is in one move away from game_map[x][y] and has less or equal halite """
    # m = game map
    n = get_c(y - 1)
    e = get_c(x + 1)
    s = get_c(y + 1)
    w = get_c(x - 1)
    if (
            (m[x][n]["ship"] != player and m[x][n]["ship"] != None and m[x][n]["ship_cargo"] <= cargo) or
            (m[x][s]["ship"] != player and m[x][s]["ship"] != None and m[x][s]["ship_cargo"] <= cargo) or
            (m[e][y]["ship"] != player and m[e][y]["ship"] != None and m[e][y]["ship_cargo"] <= cargo) or
            (m[w][y]["ship"] != player and m[w][y]["ship"] != None and m[w][y]["ship_cargo"] <= cargo)
        ):
        return True
    return False

def spawn_ship(actions, s_env, ships_amount, i):
    """ spawn ship, if possible """
    if s_env["swarm_halite"] >= conf.spawnCost and ships_amount < s_env["ships_max_amount"]:
        x = s_env["swarm_shipyards_coords"][i][0]
        y = s_env["swarm_shipyards_coords"][i][1]
        # if there is currently no ship at shipyard
        if clear(x, y, s_env["obs"].player, s_env["map"]):
            s_env["swarm_halite"] -= conf.spawnCost
            actions[s_env["shipyards_keys"][i]] = "SPAWN"
            s_env["map"][x][y]["ship"] = s_env["obs"].player
            ships_amount += 1
        return True, ships_amount
    return False, ships_amount

def this_is_new_ship(s_env, i):
    """ add this ship to ships_data """
    global movement_tactics_index
    ships_data[s_env["ships_keys"][i]] = {
        "moves_done": 0,
        "ship_max_moves": 3,
        "directions": movement_tactics[movement_tactics_index]["directions"],
        # coords of target if ship is launched as a torpedo
        "target_coords": None,
        "directions_index": 0
    }
    movement_tactics_index += 1
    if movement_tactics_index >= movement_tactics_amount:
        movement_tactics_index = 0
        
def send_as_torpedo(x_initial, y_initial, actions, s_env, i):
    """
        send this ship as a torpedo to closest shipyard of the player that is one position ahead of the Swarm
        or one position below, if Swarm is the leader
    """
    if ships_data[s_env["ships_keys"][i]]["target_coords"] == None:
        # minimal ships amount to launch ship as a torpedo
        if len(s_env["ships_keys"]) > 10 and s_env["torpedoes_amount"] < torpedoes_max_amount:
            for j in range(len(torpedo_targets)):
                if torpedo_targets[j]["player"] == s_env["obs"].player:
                    target_index = j - 1 if j > 0 else j + 1
                    if len(torpedo_targets[target_index]["shipyards"]) > 0:
                        coords = get_closest_coords(x_initial, y_initial, s_env, torpedo_targets[target_index]["shipyards"])
                        ships_data[s_env["ships_keys"][i]]["target_coords"] = coords
                    else:
                        return False
        else:
            return False
    x = ships_data[s_env["ships_keys"][i]]["target_coords"]["x"]
    y = ships_data[s_env["ships_keys"][i]]["target_coords"]["y"]
    if move_to_cell(x, y, x_initial, y_initial, actions, s_env, i):
        return True
    else:
        return False

def proceed_as_torpedo(x_initial, y_initial, actions, s_env, i):
    """ proceed to the target, if ship is a torpedo """
    if ships_data[s_env["ships_keys"][i]]["target_coords"] != None:
        x = ships_data[s_env["ships_keys"][i]]["target_coords"]["x"]
        y = ships_data[s_env["ships_keys"][i]]["target_coords"]["y"]
        # if target coords reached and are empty
        if x == x_initial and y == y_initial:
            ships_data[s_env["ships_keys"][i]]["target_coords"] = None
        elif move_to_cell(x, y, x_initial, y_initial, actions, s_env, i):
            return True
    return False

def this_is_last_step(x, y, actions, s_env, i):
    """ actions of ship, if it is last step """
    if s_env["obs"].step == (conf.episodeSteps - 2) and s_env["ships_values"][i][1] >= conf.convertCost:
        actions[s_env["ships_keys"][i]] = "CONVERT"
        s_env["map"][x][y]["ship"] = None
        return True
    return False

def to_spawn_or_not_to_spawn(s_env):
    """ to spawn, or not to spawn, that is the question """
    # get ships_max_amount to decide whether to spawn new ships or not
    ships_max_amount = s_env["average_halite"] // 5
    # if ships_max_amount is less than minimal allowed amount of ships in the Swarm
    if ships_max_amount < ships_min_amount:
        ships_max_amount = ships_min_amount
    return ships_max_amount

def define_some_globals(observation, configuration):
    """ define some of the global variables """
    global conf
    global max_moves_amount
    global globals_not_defined
    conf = configuration
    max_moves_amount = 7
    # set coords of the shipyard
    start_ship_coords = list(observation.players[observation.player][2].values())[0][0]
    shipyard_coords["x"] = start_ship_coords % conf.size
    shipyard_coords["y"] = start_ship_coords // conf.size
    globals_not_defined = False

def adapt_environment(observation, configuration, s_env):
    """ adapt environment for the Swarm """
    s_env["obs"] = observation
    if globals_not_defined:
        define_some_globals(observation, configuration)
    set_map_and_average_halite(s_env)
    s_env["low_amount_of_halite"] = 4 if s_env["average_halite"] < 4 else s_env["average_halite"]
    s_env["return_threshold"] = s_env["average_halite"] * 2
    s_env["swarm_halite"] = s_env["obs"].players[s_env["obs"].player][0]
    update_map(s_env)
    s_env["ships_keys"] = list(s_env["obs"].players[s_env["obs"].player][2].keys())
    s_env["ships_values"] = list(s_env["obs"].players[s_env["obs"].player][2].values())
    s_env["shipyards_keys"] = list(s_env["obs"].players[s_env["obs"].player][1].keys())
    s_env["ships_max_amount"] = to_spawn_or_not_to_spawn(s_env)
    s_env["torpedoes_amount"] = 0
    
def actions_of_ships(actions, s_env):
    """ actions of every ship of the Swarm """
    # calculate amount of "torpedo" ships
    for i in range(len(s_env["ships_keys"])):
        if (s_env["ships_keys"][i] in ships_data and
                ships_data[s_env["ships_keys"][i]]["target_coords"] != None):
            s_env["torpedoes_amount"] += 1
    for i in range(len(s_env["swarm_ships_coords"])):
        x = s_env["swarm_ships_coords"][i][0]
        y = s_env["swarm_ships_coords"][i][1]
        # if this is a new ship
        if s_env["ships_keys"][i] not in ships_data:
            this_is_new_ship(s_env, i)
            # send this ship as a "torpedo", if possible
            if send_as_torpedo(x, y, actions, s_env, i):
                s_env["torpedoes_amount"] += 1
                continue
        # proceed to the target, if ship is a torpedo
        if proceed_as_torpedo(x, y, actions, s_env, i):
            continue
        # if it is last step
        if this_is_last_step(x, y, actions, s_env, i):
            continue
        # if ship has to return to shipyard
        if return_to_shipyard(x, y, actions, s_env, i):
            continue
        move_ship(x, y, actions, s_env, i)

def actions_of_shipyards(actions, s_env):
    """ actions of every shipyard of the Swarm """
    ships_amount = len(s_env["ships_keys"])
    # spawn ships from every shipyard, if possible
    for i in range(len(s_env["shipyards_keys"])):
        # spawn a ship
        ok, ships_amount = spawn_ship(actions, s_env, ships_amount, i)
        if not ok:
            break


#GLOBAL_VARIABLES#############################################
conf = None
# max amount of moves in one direction before turning
max_moves_amount = None
# object with ship ids and their data
ships_data = {}
# max amount of "torpedo" ships
torpedoes_max_amount = 1
# list of torpedo targets
torpedo_targets = []
# initial movement_tactics index
movement_tactics_index = 0
# minimum amount of ships that should be in the Swarm at any time
ships_min_amount = 3
# coords of the shipyard
shipyard_coords = {"x": None, "y": None}
# not all global variables are defined
globals_not_defined = True

# list of directions
directions_list = [
    {
        "direction": "NORTH",
        "x": lambda z: z,
        "y": lambda z: get_c(z - 1)
    },
    {
        "direction": "EAST",
        "x": lambda z: get_c(z + 1),
        "y": lambda z: z
    },
    {
        "direction": "SOUTH",
        "x": lambda z: z,
        "y": lambda z: get_c(z + 1)
    },
    {
        "direction": "WEST",
        "x": lambda z: get_c(z - 1),
        "y": lambda z: z
    }
]

# list of movement tactics
movement_tactics = [
    # N -> E -> S -> W
    {"directions": get_directions(0, 1, 2, 3)},
    # S -> E -> N -> W
    {"directions": get_directions(2, 1, 0, 3)},
    # N -> W -> S -> E
    {"directions": get_directions(0, 3, 2, 1)},
    # S -> W -> N -> E
    {"directions": get_directions(2, 3, 0, 1)},
    # E -> N -> W -> S
    {"directions": get_directions(1, 0, 3, 2)},
    # W -> S -> E -> N
    {"directions": get_directions(3, 2, 1, 0)},
    # E -> S -> W -> N
    {"directions": get_directions(1, 2, 3, 0)},
    # W -> N -> E -> S
    {"directions": get_directions(3, 0, 1, 2)}
]
movement_tactics_amount = len(movement_tactics)


#THE_SWARM####################################################
def swarm_agent(observation, configuration):
    """ RELEASE THE SWARM!!! """
    # s_env -> swarm environment
    s_env = {}
    actions = {}
    adapt_environment(observation, configuration, s_env)
    actions_of_ships(actions, s_env)
    actions_of_shipyards(actions, s_env)
    return actions

Overwriting swarm.py


From [980-lb-mine-agent-more-ships](https://www.kaggle.com/code/kamaljain77/980-lb-mine-agent-more-ships)

In [12]:
%%writefile powerful_swarm.py
import time
import copy
import sys
import math
import collections
import pprint
import numpy as np
import scipy.optimize
import scipy.ndimage
from kaggle_environments.envs.halite.helpers import *
import kaggle_environments
import random
'''
Initialization code can run when the file is loaded.  The first call to agent() is allowed 30 sec
The agent function is the last function in the file (does not matter its name)
agent must run in less than 6 sec
Syntax errors when running the file do not cause any message, but cause your agent to do nothing

'''
CONFIG_MAX_SHIPS = 40

#print('kaggle version',kaggle_environments.__version__)
#### Global variables
all_actions = [
    ShipAction.NORTH, ShipAction.EAST, ShipAction.SOUTH, ShipAction.WEST
]
all_dirs = [Point(0, 1), Point(1, 0), Point(0, -1), Point(-1, 0)]
start = None
num_shipyard_targets = 4
size = None
# Will keep track of whether a ship is collecting halite or carrying cargo to a shipyard
ship_target = {}  # where to go to collect
me = None
did_init = False
quiet = False
C = None


class Obj:
    pass


# will hold global data for this turn, updating as we set actions.
# E.g. number of ships, amount of halite
# taking into account the actions set so far.  Also max_ships, etc.
turn = Obj()
### Data
#turns_optimal[CHratio, round_trip_travel] for mining
#See notebook on optimal mining kaggle.com/solverworld/optimal-mining
turns_optimal = np.array(
    [[0, 2, 3, 4, 4, 5, 5, 5, 6, 6, 6, 6, 6, 7, 7, 7, 7, 7, 7, 7, 8],
     [0, 1, 2, 3, 3, 4, 4, 4, 5, 5, 5, 5, 6, 6, 6, 6, 6, 6, 7, 7, 7],
     [0, 0, 2, 2, 3, 3, 4, 4, 4, 5, 5, 5, 5, 5, 6, 6, 6, 6, 6, 6, 7],
     [0, 0, 1, 2, 2, 3, 3, 4, 4, 4, 4, 5, 5, 5, 5, 5, 6, 6, 6, 6, 6],
     [0, 0, 0, 1, 2, 2, 3, 3, 3, 4, 4, 4, 4, 4, 5, 5, 5, 5, 5, 5, 6],
     [0, 0, 0, 0, 0, 1, 2, 2, 2, 3, 3, 3, 3, 4, 4, 4, 4, 4, 5, 5, 5],
     [0, 0, 0, 0, 0, 0, 0, 1, 1, 2, 2, 2, 3, 3, 3, 3, 3, 4, 4, 4, 4],
     [0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1, 1, 1, 2, 2, 2, 2, 2, 3, 3, 3],
     [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1, 1, 1, 1, 1, 2, 2],
     [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 1],
     [0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0, 0]])


#### Functions
def print_enemy_ships(board):
    print('\nEnemy Ships')
    for ship in board.ships.values():
        if ship.player_id != me.id:
            print('{:6}  {} halite {}'.format(ship.id, ship.position,
                                              ship.halite))


def print_actions(board):
    print('\nShip Actions')
    for ship in me.ships:
        print('{:6}  {}  {} halite {}'.format(ship.id, ship.position,
                                              ship.next_action, ship.halite))
    print('Shipyard Actions')
    for sy in me.shipyards:
        print('{:6}  {}  {}'.format(sy.id, sy.position, sy.next_action))


def print_none(*args):
    pass


def compute_max_ships(step):
    #This needs to be tuned, perhaps based on amount of halite left
    if step < 200:
        return CONFIG_MAX_SHIPS
    elif step < 300:
        return CONFIG_MAX_SHIPS - 4
    elif step < 350:
        return CONFIG_MAX_SHIPS - 10
    else:
        return CONFIG_MAX_SHIPS - 20


def set_turn_data(board):
    #initialize the global turn data for this turn
    turn.num_ships = len(me.ships)
    turn.max_ships = compute_max_ships(board.step)
    turn.total_halite = me.halite
    #this is matrix of halite in cells
    turn.halite_matrix = np.reshape(
        board.observation['halite'],
        (board.configuration.size, board.configuration.size))
    turn.num_shipyards = len(me.shipyards)
    #compute enemy presence and enemy halite matrices
    turn.EP, turn.EH, turn.ES = gen_enemy_halite_matrix(board)
    #filled in by shipid as a ship takes up a square
    turn.taken = {}
    turn.last_episode = (board.step == (board.configuration.episode_steps - 2))


def init(obs, config):
    #This is only called on first call to agent()
    #Do initalization things
    global size
    global print
    if hasattr(config, 'myval') and config.myval == 9 and not quiet:
        #we are called locally, so leave prints OK
        pass
    else:
        #we are called in competition, quiet output
        print = print_none
        pprint.pprint = print_none
    size = config.size


def limit(x, a, b):
    if x < a:
        return a
    if x > b:
        return b
    return x


def num_turns_to_mine(C, H, rt_travel):
    #How many turns should we plan on mining?
    #C=carried halite, H=halite in square, rt_travel=steps to square and back to shipyard
    if C == 0:
        ch = 0
    elif H == 0:
        ch = turns_optimal.shape[0]
    else:
        ch = int(math.log(C / H) * 2.5 + 5.5)
        ch = limit(ch, 0, turns_optimal.shape[0] - 1)
    rt_travel = int(limit(rt_travel, 0, turns_optimal.shape[1] - 1))
    return turns_optimal[ch, rt_travel]


def halite_per_turn(carrying, halite, travel, min_mine=1):
    #compute return from going to a cell containing halite, using optimal number of mining steps
    #returns halite mined per turn, optimal number of mining steps
    #Turns could be zero, meaning it should just return to a shipyard (subject to min_mine)
    turns = num_turns_to_mine(carrying, halite, travel)
    if turns < min_mine:
        turns = min_mine
    mined = carrying + (1 - .75**turns) * halite
    return mined / (travel + turns), turns


def move(pos, action):
    ret = None
    #return new Position from pos when action is applied
    if action == ShipAction.NORTH:
        ret = pos + Point(0, 1)
    if action == ShipAction.SOUTH:
        ret = pos + Point(0, -1)
    if action == ShipAction.EAST:
        ret = pos + Point(1, 0)
    if action == ShipAction.WEST:
        ret = pos + Point(-1, 0)
    if ret is None:
        ret = pos
    #print('move pos {} {} => {}'.format(pos,action,ret))
    return ret % size


def dirs_to(p1, p2, size=21):
    #Get the actions you should take to go from Point p1 to Point p2
    #using shortest direction by wraparound
    #Args: p1: from Point
    #      p2: to Point
    #      size:  size of board
    #returns: list of directions, tuple (deltaX,deltaY)
    #The list is of length 1 or 2 giving possible directions to go, e.g.
    #to go North-East, it would return [ShipAction.NORTH, ShipAction.EAST], because
    #you could use either of those first to go North-East.
    #[None] is returned if p1==p2 and there is no need to move at all
    deltaX, deltaY = p2 - p1
    if abs(deltaX) > size / 2:
        #we wrap around
        if deltaX < 0:
            deltaX += size
        elif deltaX > 0:
            deltaX -= size
    if abs(deltaY) > size / 2:
        #we wrap around
        if deltaY < 0:
            deltaY += size
        elif deltaY > 0:
            deltaY -= size
    #the delta is (deltaX,deltaY)
    ret = []
    if deltaX > 0:
        ret.append(ShipAction.EAST)
    if deltaX < 0:
        ret.append(ShipAction.WEST)
    if deltaY > 0:
        ret.append(ShipAction.NORTH)
    if deltaY < 0:
        ret.append(ShipAction.SOUTH)
    if len(ret) == 0:
        ret = [None]  # do not need to move at all
    return ret, (deltaX, deltaY)


def shipyard_actions():
    #spawn a ship as long as there is no ship already moved to this shipyard
    for sy in me.shipyards:
        if turn.num_ships < turn.max_ships:
            if turn.total_halite >= 500 and sy.position not in turn.taken:
                #spawn one
                sy.next_action = ShipyardAction.SPAWN
                turn.taken[sy.position] = 1
                turn.num_ships += 1
                turn.total_halite -= 500


def gen_enemy_halite_matrix(board):
    #generate matrix of enemy positions:
    #EP=presence of enemy ship
    #EH=amount of halite in enemy ships
    #ES=presence of enemy shipyards
    EP = np.zeros((size, size))
    EH = np.zeros((size, size))
    ES = np.zeros((size, size))
    for id, ship in board.ships.items():
        if ship.player_id != me.id:
            EH[ship.position.y, ship.position.x] = ship.halite
            EP[ship.position.y, ship.position.x] = 1
    for id, sy in board.shipyards.items():
        if sy.player_id != me.id:
            ES[sy.position.y, sy.position.x] = 1
    return EP, EH, ES


def dist(a, b):
    #Manhattan distance of the Point difference a to b, considering wrap around
    action, step = dirs_to(a, b, size=21)
    return abs(step[0]) + abs(step[1])


def nearest_shipyard(pos):
    #return distance, position of nearest shipyard to pos.  100,None if no shipyards
    mn = 100
    best_pos = None
    for sy in me.shipyards:
        d = dist(pos, sy.position)
        if d < mn:
            mn = d
            best_pos = sy.position
    return mn, best_pos


def assign_targets(board, ships):
    #Assign the ships to a cell containing halite optimally
    #set ship_target[ship_id] to a Position
    #We assume that we mine halite containing cells optimally or return to deposit
    #directly if that is optimal, based on maximizing halite per step.
    #Make a list of pts containing cells we care about, this will be our columns of matrix C
    #the rows are for each ship in collect
    #computes global dict ship_tagert with shipid->Position for its target
    #global ship targets should already exist
    old_target = copy.copy(ship_target)
    ship_target.clear()
    if len(ships) == 0:
        return
    halite_min = 50
    pts1 = []
    pts2 = []
    for pt, c in board.cells.items():
        assert isinstance(pt, Point)
        if c.halite > halite_min:
            pts1.append(pt)
    #Now add duplicates for each shipyard - this is directly going to deposit
    for sy in me.shipyards:
        for i in range(num_shipyard_targets):
            pts2.append(sy.position)
    #this will be the value of assigning C[ship,pt]
    C = np.zeros((len(ships), len(pts1) + len(pts2)))
    #this will be the optimal mining steps we calculated
    for i, ship in enumerate(ships):
        for j, pt in enumerate(pts1 + pts2):
            #two distances: from ship to halite, from halite to nearest shipyard
            d1 = dist(ship.position, pt)
            d2, shipyard_position = nearest_shipyard(pt)
            if shipyard_position is None:
                #don't know where to go if no shipyard
                d2 = 1
            #value of target is based on the amount of halite per turn we can do
            my_halite = ship.halite
            if j < len(pts1):
                #in the mining section
                v, mining = halite_per_turn(my_halite, board.cells[pt].halite,
                                            d1 + d2)
                #mining is no longer 0, due to min_mine (default)
            else:
                #in the direct to shipyard section
                if d1 > 0:
                    v = my_halite / d1
                else:
                    #we are at a shipyard
                    v = 0
            if board.cells[pt].ship and board.cells[pt].ship.player_id != me.id:
                #if someone else on the cell, see how much halite they have
                #enemy ship
                enemy_halite = board.cells[pt].ship.halite
                if enemy_halite <= my_halite:
                    v = -1000  # don't want to go there
                else:
                    if d1 < 5:
                        #attack or scare off if reasonably quick to get there
                        v += enemy_halite / (
                            d1 + 1)  # want to attack them or scare them off
            #print('shipid {} col {} is {} with {:8.1f} score {:8.2f}'.format(ship.id,j, pt,board.cells[pt].halite,v))
            C[i, j] = v
    print('C is {}'.format(C.shape))
    #Compute the optimal assignment
    row, col = scipy.optimize.linear_sum_assignment(C, maximize=True)
    #so ship row[i] is assigned to target col[j]
    #print('got row {} col {}'.format(row,col))
    #print(C[row[0],col[0]])
    pts = pts1 + pts2
    for r, c in zip(row, col):
        ship_target[ships[r].id] = pts[c]
    #print out results
    print('\nShip Targets')
    print('Ship      position          target')
    for id, t in ship_target.items():
        st = ''
        ta = ''
        if board.ships[id].position == t:
            st = 'MINE'
        elif len(me.shipyards) > 0 and t == me.shipyards[0].position:
            st = 'SHIPYARD'
        if id not in old_target or old_target[id] != ship_target[id]:
            ta = ' NEWTARGET'
        print(
            '{0:6}  at ({1[0]:2},{1[1]:2})  assigned ({2[0]:2},{2[1]:2}) h {3:3} {4:10} {5:10}'
            .format(id, board.ships[id].position, t, board.cells[t].halite, st,
                    ta))

    return


def make_avoidance_matrix(myship_halite):
    #make a matrix of True where we want to avoid, uses
    #turn.EP=enemy position matrix
    #turn.EH=enemy halite matrix
    #turn.ES=enemy shipyard matrix
    filter = np.array([[0, 1, 0], [1, 1, 1], [0, 1, 0]])
    bad_ship = np.logical_and(turn.EH <= myship_halite, turn.EP)
    avoid = scipy.ndimage.convolve(bad_ship, filter, mode='wrap', cval=0.0)
    avoid = np.logical_or(avoid, turn.ES)
    return avoid


def make_attack_matrix(myship_halite):
    #make a matrix of True where we would want to move to attack an enemy ship
    #for now, we just move to where the ship is.
    #turn.EP=enemy position matrix
    #turn.EH=enemy halite matrix
    attack = np.logical_and(turn.EH > myship_halite, turn.EP)
    #print('attack',attack)
    return attack


def get_max_halite_ship(board, avoid_danger=True):
    #Return my Ship carrying max halite, or None if no ships
    #NOTE: creating avoid matrix again!
    mx = -1
    the_ship = None
    for ship in me.ships:
        x = ship.position.x
        y = ship.position.y
        avoid = make_avoidance_matrix(ship.halite)
        if ship.halite > mx and (not avoid_danger or not avoid[y, x]):
            mx = ship.halite
            the_ship = ship
    return the_ship


def remove_dups(p):
    #remove duplicates from a list without changing order
    #Not efficient for long lists
    ret = []
    for x in p:
        if x not in ret:
            ret.append(x)
    return ret


def matrix_lookup(matrix, pos):
    return matrix[pos.y, pos.x]
    
    
def ship_converts(board):
    def converts(ship, turn):
        ship.next_action = ShipAction.CONVERT
        turn.taken[ship.position] = 1
        turn.num_shipyards += 1
        turn.total_halite -= 500

    #if no shipyard, convert the ship carrying max halite unless it is in danger
    if turn.num_shipyards == 0 and not turn.last_episode:
        ship = get_max_halite_ship(board)
        if ship is not None:
            if ship.halite + turn.total_halite > 500:
                converts(ship, turn)
                
    #Now check the rest to see if they should convert
    for ship in me.ships:
        if ship.next_action:
            continue
        #CHECK if in danger without escape, convert if h>500
        avoid = make_avoidance_matrix(ship.halite)
        z = [matrix_lookup(avoid, move(ship.position, a)) for a in all_actions]
        if np.all(z) and ship.halite > 500:
            converts(ship, turn)
            print('ship id {} no escape converting'.format(ship.id))
            
        #CHECK if last step and > 500 halite, convert
        if turn.last_episode and ship.halite > 500:
            converts(ship, turn)

    # Generate shipyard from the best ship
    if turn.num_shipyards <= 4 and turn.num_ships > 10 + turn.num_shipyards * 5 and board.step < 300:
        max_halite_score = 0
        max_ship = None
        for ship in me.ships:
            halite_score = 0
            if ship.next_action: continue

            for pt, c in board.cells.items():
                d = dist(ship.position, pt)
                if d == 0: # Substract score if the position have much halite
                    halite_score -= c.halite
                else:
                    halite_score += c.halite / d

            # Substract if shipyards around
            for sy in me.shipyards:
                d = dist(ship.position, sy.position)
                if d == 0: # shipyard here
                    halite_score -= 1000000
                else:
                    halite_score -= 100 / d

            if max_halite_score < halite_score:
                max_halite_score = halite_score
                max_ship = ship

        if max_ship:
            converts(max_ship, turn)

    
def ship_moves(board):
    ships = [ship for ship in me.ships if ship.next_action is None]
    #update ship_target
    assign_targets(board, ships)
    #For all ships without a target, we give them a random movement (we will check below if this
    actions = {}  # record actions for each ship
    for ship in ships:
        if ship.id in ship_target:
            a, delta = dirs_to(ship.position, ship_target[ship.id], size=size)
            actions[ship.id] = a
        else:
            actions[ship.id] = [random.choice(all_actions)]

    for ship in ships:
        action = None
        x = ship.position
        #generate matrix of places to attack and places to avoid
        avoid = make_avoidance_matrix(ship.halite)
        attack = make_attack_matrix(ship.halite)
        #see if there is a attack options
        action_list = actions[ship.id] + [None] + all_actions
        #see if we should add an attack diversion to our options
        #NOTE: we will avoid attacking a ship that is on the avoid spot - is this a good idea?
        for a in all_actions:
            m = move(x, a)
            if attack[m.y, m.x]:
                print('ship id {} attacking {}'.format(ship.id, a))
                action_list.insert(0, a)
                break
        #now try the options, but don't bother repeating any
        action_list = remove_dups(action_list)
        for a in action_list:
            m = move(x, a)
            if avoid[m.y, m.x]:
                print('ship id {} avoiding {}'.format(ship.id, a))
            if m not in turn.taken and not avoid[m.y, m.x]:
                action = a
                break
        ship.next_action = action
        turn.taken[m] = 1


# Returns the commands we send to our ships and shipyards, must be last function in file
def agent(obs, config):
    global size
    global start
    global prev_board
    global me
    global did_init
    #Do initialization 1 time
    start_step = time.time()
    if start is None:
        start = time.time()
    if not did_init:
        init(obs, config)
        did_init = True
    board = Board(obs, config)
    me = board.current_player
    set_turn_data(board)
    print('==== step {} sim {}'.format(board.step, board.step + 1))
    print('ships {} shipyards {}'.format(turn.num_ships, turn.num_shipyards))
    print_enemy_ships(board)
    ship_converts(board)
    ship_moves(board)
    shipyard_actions()
    print_actions(board)
    print('time this turn: {:8.3f} total elapsed {:8.3f}'.format(
        time.time() - start_step,
        time.time() - start))
    return me.next_actions

Overwriting powerful_swarm.py


In [13]:
from kaggle_environments import evaluate, make
import time
import numpy as np

env = make("halite", debug=True)

In [14]:
print(*env.agents)

random


In [6]:
%time evaluate("halite", agents=["imitation_learning.py", "swarm.py"])

CPU times: user 22.4 s, sys: 1.8 s, total: 24.2 s
Wall time: 31.8 s


[[33856, 227]]

In [20]:
def get_win_percentage(agent1, agent2, n_round = 100):
    print("Starting Evaluation")
    outcomes = []
    a1_win = 0
    a2_win = 0
    a1_err = 0
    a2_err = 0
    for _ in range(n_round//2):
        o = evaluate("halite", agents=[agent1, agent2])
        [a,b] = o[0]
        if a == None :
            a1_err += 1
        if b == None :
            a2_err += 1
        if a > b:
            a1_win += 1
        if b > a:
            a2_win +=1
    
    for _ in range(n_round -n_round//2):
        o += [[b, a] for [a,b] in evaluate("halite", agents=[agent2, agent1])]
        [a,b] = o[0]
        if a == None :
            a1_err += 1
        if b == None :
            a2_err += 1
        if a > b:
            a1_win += 1
        if b > a:
            a2_win +=1
    print("All fights are done")
    
    
    print("Agent 1 Win Percentage:", np.round(a1_win/n_round, 2))
    print("Agent 2 Win Percentage:", np.round(a2_win/n_round, 2))
    print("Number of Invalid Plays by Agent 1:", a1_err)
    print("Number of Invalid Plays by Agent 2:", a2_err)
        
            
    

In [21]:
#%time get_win_percentage("imitation_learning.py", "swarm.py")

Starting Evaluation
All fights are done
Agent 1 Win Percentage: 1.0
Agent 2 Win Percentage: 0.0
Number of Invalid Plays by Agent 1: 0
Number of Invalid Plays by Agent 2: 0
CPU times: user 41.2 s, sys: 53.9 ms, total: 41.2 s
Wall time: 41.4 s


In [ ]:
%time get_win_percentage("imitation_learning.py", "powerful_swarm.py")

In [14]:
env.run(["imitation_learning.py", "powerful_swarm.py"])
env.render(mode="ipython", width=800, height=600)

changing model
changing model
